In [140]:
import scipy.io as sio
import json
import numpy as np

edges_multi = sio.loadmat('imagenet-multi-weight-graph-raw.mat')

base_graph = json.load(open('imagenet-induced-graph.json')) # 200082条边
wnids = base_graph['wnids']  # wordnet id
vectors = np.array(base_graph['vectors'])  # 语义特征
_, _, _, edges, hops, semantic_dis, visual_dis = edges_multi.values()
from sklearn.preprocessing import MinMaxScaler 
scaler = MinMaxScaler()
hops = scaler.fit_transform(hops.reshape(-1,1))
hops = 1-hops
semantic_dis = scaler.fit_transform(semantic_dis.reshape(-1,1))
semantic_dis = 1-semantic_dis

In [145]:
def get_input(edge, dis, hop):
    a, b = edge
    return np.hstack((vectors[a], vectors[b], dis, hop))
train_x = []
train_y = []
for i in range(edges.shape[0]):
# for i in range(10):
    x = get_input(edges[i], hops[i], semantic_dis[i])
    y = visual_dis[0][i]
    if y == -1.0:
        continue
    else:
        train_x.append(x)
        train_y.append(y)
train_x = np.stack((train_x))
train_y = np.stack((train_y))


In [277]:
import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.model_selection import train_test_split
x_train, x_val, y_train, y_val = train_test_split(train_x, train_y, test_size=0.2, random_state=17)
dataset_train = TensorDataset(
    torch.from_numpy(x_train),
    torch.from_numpy(y_train)
)
dataset_val = TensorDataset(
    torch.from_numpy(x_val),
    torch.from_numpy(y_val)
)
print('train_size:', x_train.shape)
print('val_size:', x_val.shape)
train_loader = DataLoader(
    dataset=dataset_train, batch_size=100, shuffle=True, num_workers=2
)
val_loader = DataLoader(
    dataset=dataset_val, batch_size=100, shuffle=False, num_workers=2
)

train_size: (51803, 602)
val_size: (12951, 602)


In [141]:
from torch import nn
class Model(nn.Module):
    def __init__(self, input_dim):
        super(Model, self).__init__()
        self.fwd = nn.Sequential(
            nn.Linear(input_dim, 256),
            nn.ReLU(),
            nn.Linear(256, 1))
    def forward(self, x):
        return self.fwd(x)

In [142]:
import torch
from tqdm import trange
import copy
mse_loss = nn.MSELoss()
model = Model(x_train.shape[-1]).cuda()
opt = torch.optim.Adam(model.parameters(), lr=1e-4, weight_decay=1e-3)
model.train()
val_min = float('INF')
save_model = None
with torch.set_grad_enabled(True):
    pbar = trange(300)
    for epoch in pbar:
        total_num = 0
        running_loss = 0.0
        # Iterate over data.
        for x, y in train_loader:
            x, y = x.float().cuda(), y.float().view(-1,1).cuda()
            opt.zero_grad()
            out = model(x)  # semantic -> visual space
            loss = mse_loss(out, y)
            loss.backward()
            opt.step()
            # statistics loss and acc every epoch
            running_loss += loss.item()
            total_num += x.shape[0]
            # Iterate over data.
        train_loss = running_loss/total_num
        model.eval()
        total_num = 0
        running_loss = 0.0
        for x, y in val_loader:
            x, y = x.float().cuda(), y.float().view(-1,1).cuda()
            out = model(x)  # semantic -> visual space
            loss = mse_loss(out, y)
            running_loss += loss.item()
            total_num += x.shape[0]
        val_loss = running_loss/total_num
        pbar.set_description(f"train loss: {train_loss}; val loss: {val_loss}")  # 如果只有这一个表示单独显示，若有2个表示交替显示这2个，经过实验最后显示最后一个nihao: 551560000
        if val_loss < val_min:
            val_min = val_loss
            save_model = copy.deepcopy(model)
            print('save model at val_loss %f'%val_loss)
        

NameError: name 'x_train' is not defined

In [144]:
# torch.save(save_model.state_dict(),'predict_visual_dis_model.pth')
model = Model(602).cuda()
model.load_state_dict(torch.load('predict_visual_dis_model.pth'))

IncompatibleKeys(missing_keys=[], unexpected_keys=[])

In [146]:
inf_y = []
model.eval()
for i in range(edges.shape[0]):
    x = get_input(edges[i], hops[i], semantic_dis[i])
    y = visual_dis[0][i]
    if y == -1.0:
        pred = model(torch.tensor(x).float().cuda()).cpu().tolist()[0]
        inf_y.append(pred)
    else:
        inf_y.append(y)
visual_dis_pred = scaler.fit_transform(np.vstack(inf_y))
visual_dis_pred = 1-visual_dis_pred

# 将权重矩阵去掉训练类中的互连边，否则影响训练效果

In [288]:
import scipy.io as sio
sio.savemat('imagenet-multi-weight-graph-pred-visual.mat', {
    'edges':edges,
    'hops':hops,
    'semantic_dis':semantic_dis,
    'visual_dis':visual_dis_pred})


In [292]:
# 去掉训练类间的边
edges_save = []
hops_save = []
semantic_dis_save = []
visual_dis_pred_save = []

for i in range(edges.shape[0]):
    a, b = edges[i]
    if a < 1000 and b < 1000 and a != b:
        continue
    else:
        edges_save.append(edges[i])
        hops_save.append(hops[i])
        semantic_dis_save.append(semantic_dis[i])
        visual_dis_pred_save.append(visual_dis_pred[i])

In [294]:
import scipy.io as sio
sio.savemat('imagenet-multi-weight-graph-pred-visual-del-train.mat', {
    'edges':edges_save,
    'hops':hops_save,
    'semantic_dis':semantic_dis_save,
    'visual_dis':visual_dis_pred_save})

# 将权重矩阵转为上三角

In [1]:
import scipy.io as sio
mat = sio.loadmat('imagenet-multi-weight-graph-pred-visual-del-train.mat')
edges = mat['edges']
hops = mat['hops']
semantic_dis = mat['semantic_dis']
visual_dis_pred = mat['visual_dis']

In [15]:
# 去掉训练类间的边
edges_save = []
hops_save = []
semantic_dis_save = []
visual_dis_pred_save = []

for i in range(edges.shape[0]):
    a, b = edges[i]
    ee = [a, b] if a<=b else [b, a]
    edges_save.append(ee)
    hops_save.append(hops[i])
    semantic_dis_save.append(semantic_dis[i])
    visual_dis_pred_save.append(visual_dis_pred[i])

In [17]:
n=32324
adjs = {}
for i in range(n):
    adjs[i] = []
for u, v in edges_save:
    adjs[u].append(v)
    
for k, v in adjs.items():
    for a in v:
        if k in adjs[a] and k!=a:
            print(k, v,'->', a, adjs[a])    

for edge in edges_save:
    a,b = edge
    if a>b:
        print(a,b)

In [20]:
import scipy.io as sio
sio.savemat('imagenet-multi-weight-graph-upper-triangular.mat', {
    'edges':edges_save,
    'hops':hops_save,
    'semantic_dis':semantic_dis_save,
    'visual_dis':visual_dis_pred_save})

# 通过语义属性为其他边预测hops，增加边。


In [425]:
import scipy.io as sio
mat = sio.loadmat('imagenet-aux-21K-graph.mat')
edges = mat['edges'].squeeze()
hops = mat['hops'].reshape(-1,1)
semantic_dis = mat['semantic_dis'].squeeze()
visual_dis = mat['visual_dis'].squeeze()
hops_map = {hop:idx for idx, hop in enumerate(sorted(list(set(hops.squeeze())),reverse=True))}

In [449]:
from sklearn.metrics.pairwise import pairwise_distances
from sklearn.linear_model import LogisticRegression
def cos_dis(a, b):
    return pairwise_distances([a,b], metric='cosine')[0][1]

base_graph = json.load(open('imagenet-induced-graph.json')) 
wnids = base_graph['wnids']  # wordnet id
vectors = np.array(base_graph['vectors'])  # 语义特征

vec_dict = dict(zip(list(range(len(wnids))), vectors))
train_dis = [np.hstack((vec_dict[a], vec_dict[b])) for a,b in edges if a!=b]
train_dis = np.stack(train_dis)

train_y = np.array(list(map(lambda h:hops_map[h], hops.squeeze())))
train_y = train_y[np.argwhere(train_y!=0)].squeeze()

In [450]:
train_y.shape

(81351,)

In [451]:
Counter(train_y)

Counter({1: 18638, 2: 18482, 3: 17086, 4: 15221, 5: 11924})

In [452]:
js = json.load(open('imagenet-split.json'))
tr = js['train']
ts = js['test']
id_dict = dict(zip(wnids, list(range(len(wnids)))))
nodes = tr+ts
nodes_id = [id_dict[id] for id in nodes]
n = len(nodes_id)
clf = LogisticRegression(random_state=0, max_iter=1000).fit(train_dis, train_y)

In [453]:
clf.classes_

array([1, 2, 3, 4, 5])

In [454]:
adjs = {}
for i in range(n):
    adjs[i] = []
for u, v in edges:
    adjs[u].append(v)

vec_dict = dict(zip(list(range(n)), vectors))
# vec_dict = dict(zip(wnids, vectors))
inf_edge = []
inf_x = []
add_edges = []
pred_hops = np.array([])
import tqdm
for i in range(n):
    print(i)
    neigh = adjs[i]
    target = [[i, j] for j in range(1000, n) if j not in neigh]
    target_vec = [np.hstack((vec_dict[s], vec_dict[t])) for s, t in target]
#     pred_hop = clf.predict(target_vec)
    pred_hop = clf.predict_proba(target_vec)[:,0]  # 预测属于第二类的概率，即仅为1跳的边
    selected1 = np.argsort(pred_hop)[::-1][:10]  # 选择预测概率最大的20条边
    selected2 = np.where(pred_hop>0.8)[0]  # 预测概率大于0.8
    selected = np.intersect1d(selected1, selected2)    
    save = np.array(target)[selected]
    for edge in save:
        add_edges.append(edge)
    if len(selected)>0:
        print(f'save {len(selected)} edges','max_prob', pred_hop[selected[0]],'min_prob',pred_hop[selected[-1]])


0
save 10 edges max_prob 0.9625835860370928 min_prob 0.9554927299924028
1
save 10 edges max_prob 0.8798326430962422 min_prob 0.8527778168173451
2
save 10 edges max_prob 0.8777091924181345 min_prob 0.8820572747901301
3
save 10 edges max_prob 0.882794592797321 min_prob 0.8836554865356969
4
save 10 edges max_prob 0.837963909301602 min_prob 0.8220142657523036
5
save 10 edges max_prob 0.8603914215492435 min_prob 0.8315986339473046
6
save 6 edges max_prob 0.8094521414948089 min_prob 0.8186995767821926
7
save 10 edges max_prob 0.908663657422176 min_prob 0.887564731523368
8
save 10 edges max_prob 0.9514048618977976 min_prob 0.9550173456497953
9
save 10 edges max_prob 0.9023439779054812 min_prob 0.8811373950311774
10
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
11
save 10 edges max_prob 0.9346938745665216 min_prob 0.9210022508125549
12
save 10 edges max_prob 0.8947706071730143 min_prob 0.8740497705845387
13
save 10 edges max_prob 0.9395239109786903 min_prob 0.9273120673

save 10 edges max_prob 0.9116318349650192 min_prob 0.8934577336564601
121
save 10 edges max_prob 0.9119323402684024 min_prob 0.8913068255888844
122
save 10 edges max_prob 0.9013255358447839 min_prob 0.8841576849825278
123
save 10 edges max_prob 0.8892927541978052 min_prob 0.8678306541514773
124
save 10 edges max_prob 0.9257945863931302 min_prob 0.9120964011669496
125
save 10 edges max_prob 0.886750137674199 min_prob 0.8656817248994862
126
save 10 edges max_prob 0.8436688579555403 min_prob 0.8208463021934723
127
save 10 edges max_prob 0.9245727184661858 min_prob 0.9051993297089072
128
save 10 edges max_prob 0.924787848940998 min_prob 0.9095866509551751
129
save 10 edges max_prob 0.9741105122035795 min_prob 0.9692764150415156
130
save 10 edges max_prob 0.9356397732398573 min_prob 0.9251029754162656
131
save 10 edges max_prob 0.9352755916168857 min_prob 0.9218876000455859
132
save 10 edges max_prob 0.9394121261349285 min_prob 0.927864153126224
133
save 10 edges max_prob 0.9283530429529766

236
save 10 edges max_prob 0.8921235787797773 min_prob 0.8686703687273984
237
save 10 edges max_prob 0.87408222726331 min_prob 0.8486250643295726
238
239
save 10 edges max_prob 0.8390736012457062 min_prob 0.8462656135848541
240
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
241
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
242
save 10 edges max_prob 0.9132796621786511 min_prob 0.8934419823977319
243
save 10 edges max_prob 0.8484095344398336 min_prob 0.8543597968802215
244
245
save 10 edges max_prob 0.9205833332014459 min_prob 0.9005913370886152
246
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
247
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
248
save 6 edges max_prob 0.8280175537115434 min_prob 0.8361867987362911
249
250
save 10 edges max_prob 0.8944579200049374 min_prob 0.8672069272159607
251
save 5 edges max_prob 0.8235861749379755 min_prob 0.8429769250420891
252
save 10 edges max_prob 0.8

save 10 edges max_prob 0.9145742174818914 min_prob 0.9209860019169341
357
save 10 edges max_prob 0.9303117930897858 min_prob 0.9360341694179256
358
save 10 edges max_prob 0.9394319605397758 min_prob 0.9230492235784108
359
save 7 edges max_prob 0.8303883954398463 min_prob 0.8372412548438839
360
save 10 edges max_prob 0.9051367857121089 min_prob 0.8838435177448084
361
save 10 edges max_prob 0.9118029967338859 min_prob 0.8876775406884486
362
save 10 edges max_prob 0.8390348253599345 min_prob 0.8117011447196373
363
save 10 edges max_prob 0.9134992295272419 min_prob 0.8974244330498289
364
save 10 edges max_prob 0.9165259314621698 min_prob 0.9199223377622816
365
366
save 10 edges max_prob 0.9208066362672291 min_prob 0.8964665170178903
367
save 10 edges max_prob 0.9033157965976996 min_prob 0.9088198853787538
368
369
save 10 edges max_prob 0.8982740677378924 min_prob 0.8779010461188201
370
371
save 10 edges max_prob 0.9291141076825276 min_prob 0.9112736198646239
372
save 10 edges max_prob 0.89

save 10 edges max_prob 0.9490597901507121 min_prob 0.9515354394168476
475
save 10 edges max_prob 0.8713626649057791 min_prob 0.8791873213373667
476
save 10 edges max_prob 0.9257669226215807 min_prob 0.9117612635545389
477
save 10 edges max_prob 0.8410751923759617 min_prob 0.8504526044020302
478
save 10 edges max_prob 0.9150816497227025 min_prob 0.9018552750648169
479
save 1 edges max_prob 0.8079526780126752 min_prob 0.8079526780126752
480
save 4 edges max_prob 0.8178246803110882 min_prob 0.8291159311536206
481
save 10 edges max_prob 0.9116900936125092 min_prob 0.8909471033191352
482
save 10 edges max_prob 0.8564671267508083 min_prob 0.861591540754373
483
save 10 edges max_prob 0.8795156911058278 min_prob 0.8744133540599245
484
save 10 edges max_prob 0.9222600337084844 min_prob 0.9085846843907367
485
486
save 10 edges max_prob 0.9297145732929466 min_prob 0.9166167421033613
487
488
save 10 edges max_prob 0.8390598171227179 min_prob 0.8472441813977786
489
save 10 edges max_prob 0.90221912

...

save 10 edges max_prob 0.9108700142164174 min_prob 0.8928280590184194
21327
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21328
save 10 edges max_prob 0.8605318719460547 min_prob 0.8302378490278706
21329
save 9 edges max_prob 0.8359713239108778 min_prob 0.8451754736430398
21330
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21331
save 10 edges max_prob 0.9379226185440097 min_prob 0.9280052149075102
21332
save 10 edges max_prob 0.9468828326741565 min_prob 0.9500844244315123
21333
save 10 edges max_prob 0.9407353909378617 min_prob 0.9290806874989334
21334
save 2 edges max_prob 0.8013424520928565 min_prob 0.8187758046519252
21335
save 10 edges max_prob 0.9276929730046201 min_prob 0.9105198092459661
21336
save 10 edges max_prob 0.9280641780327141 min_prob 0.9129568288039159
21337
save 10 edges max_prob 0.910587410508095 min_prob 0.8893062666157411
21338
save 10 edges max_prob 0.8381541679483445 min_prob 0.8052951816278129
21339
save 10 edges m

save 10 edges max_prob 0.9097888371872291 min_prob 0.8960636259127903
21445
save 10 edges max_prob 0.8904196133639382 min_prob 0.8729366193083801
21446
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21447
save 10 edges max_prob 0.8984125802917645 min_prob 0.9047124729760406
21448
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21449
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21450
save 10 edges max_prob 0.954030100563373 min_prob 0.9558679915714287
21451
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21452
save 10 edges max_prob 0.9627853767891112 min_prob 0.956620219422663
21453
21454
save 10 edges max_prob 0.9551440352419927 min_prob 0.9460925223697381
21455
save 10 edges max_prob 0.8852172132383206 min_prob 0.8627088496874414
21456
save 10 edges max_prob 0.8844506157091376 min_prob 0.8664944068422151
21457
21458
save 10 edges max_prob 0.8791278609451347 min_prob 0.8577230341446015
21459
sa

21560
21561
save 10 edges max_prob 0.933238128286424 min_prob 0.9179652120515882
21562
save 10 edges max_prob 0.8484940428490494 min_prob 0.8332685046520109
21563
save 10 edges max_prob 0.9368938929343702 min_prob 0.924682856347909
21564
save 10 edges max_prob 0.9536640337075929 min_prob 0.9568487706225167
21565
save 10 edges max_prob 0.9192398255176775 min_prob 0.9203165114000488
21566
save 10 edges max_prob 0.9450748532898905 min_prob 0.9332485137006254
21567
save 1 edges max_prob 0.8117606329329871 min_prob 0.8117606329329871
21568
21569
21570
save 10 edges max_prob 0.9661142538011122 min_prob 0.956769891528337
21571
save 10 edges max_prob 0.9117737241242756 min_prob 0.8908632863554014
21572
save 1 edges max_prob 0.8197412857705024 min_prob 0.8197412857705024
21573
save 10 edges max_prob 0.9561388106771432 min_prob 0.9483594584325161
21574
save 10 edges max_prob 0.8401343326633443 min_prob 0.8061421229283084
21575
save 10 edges max_prob 0.8724690110477084 min_prob 0.849562243650855


save 10 edges max_prob 0.9003303354121104 min_prob 0.8748261667622416
21683
save 10 edges max_prob 0.9018487257358263 min_prob 0.8825285707676728
21684
save 10 edges max_prob 0.8929282116231383 min_prob 0.8989584846567866
21685
save 10 edges max_prob 0.9303788231992464 min_prob 0.9158052375418418
21686
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21687
save 10 edges max_prob 0.9136868462278025 min_prob 0.8983271639734419
21688
save 1 edges max_prob 0.8081384580192332 min_prob 0.8081384580192332
21689
21690
save 10 edges max_prob 0.9089099212650527 min_prob 0.8928343460615157
21691
save 10 edges max_prob 0.8663341034759096 min_prob 0.8344669678004575
21692
save 10 edges max_prob 0.9229403378014646 min_prob 0.904370279224557
21693
21694
21695
save 10 edges max_prob 0.9245306958953604 min_prob 0.9102667988367078
21696
save 10 edges max_prob 0.8348552907694958 min_prob 0.8121514534546044
21697
save 10 edges max_prob 0.9490848115039154 min_prob 0.9380885179623943
21

save 10 edges max_prob 0.8769996007708339 min_prob 0.8446760440632243
21810
save 10 edges max_prob 0.9174046747590041 min_prob 0.9046172238297553
21811
save 10 edges max_prob 0.9737728680682409 min_prob 0.9693582941375514
21812
save 10 edges max_prob 0.912705909653038 min_prob 0.8923772748001656
21813
save 5 edges max_prob 0.817275885677489 min_prob 0.8396190566580022
21814
save 10 edges max_prob 0.8967926329351683 min_prob 0.8789631734468399
21815
save 10 edges max_prob 0.9427350086233847 min_prob 0.9314674870530671
21816
save 10 edges max_prob 0.8989903931144263 min_prob 0.8845129639786584
21817
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21818
save 10 edges max_prob 0.8806440291746194 min_prob 0.8548602907943387
21819
save 10 edges max_prob 0.8642398692390637 min_prob 0.8354208739975297
21820
save 10 edges max_prob 0.864212615437741 min_prob 0.8403264904623873
21821
save 10 edges max_prob 0.8422174963558038 min_prob 0.8064288493020006
21822
save 10 edges ma

In [455]:
sio.savemat('imagenet-multi-weight-graph-aux-edges.mat',{
    'edges':edges,
    'hops':hops,
    'semantic_dis':semantic_dis,
    'visual_dis':visual_dis,
    'wnids':nodes,
    'aux_edges':np.array(add_edges),
    'descriptions':'only 21K nodes, predict hops to add aux edges.'})

 # 只保留21K个结点的权重矩阵边，且为上三角形。

In [391]:
import scipy.io as sio
mat = sio.loadmat('imagenet-multi-weight-graph-upper-triangular.mat')
edges = mat['edges'].squeeze()
hops = mat['hops'].squeeze()
semantic_dis = mat['semantic_dis'].squeeze()
visual_dis = mat['visual_dis'].squeeze()
n = 21841
mask = []
for idx, (a, b) in enumerate(edges):
    if not (a>n or b>n):
        mask.append(idx)
sio.savemat('imagenet-aux-21K-graph.mat',{
    'edges':edges[mask],
    'hops':hops[mask],
    'semantic_dis':semantic_dis[mask],
    'visual_dis':visual_dis[mask],
    'wnids':nodes,
    'descriptions':'only 21K nodes, upper-triangular weight matrix.'})

 # 将所有edges划分成6份（取了6跳内的边）

In [395]:
mat = sio.loadmat('imagenet-aux-21K-graph.mat')
edges = mat['edges'].squeeze()
hops = mat['hops'].squeeze()
semantic_dis = mat['semantic_dis'].squeeze()
visual_dis = mat['visual_dis'].squeeze()

hops_map = {hop:idx for idx, hop in enumerate(sorted(list(set(hops.squeeze())),reverse=True))}
hops_num = len(hops_map.keys())

idx = [int(x*len(semantic_dis))-1 for x in list(np.arange(0, 1.1, 1.0/6))][1:]
semantic_ts = np.array(sorted(semantic_dis,reverse=True))[idx]
idx = [int(x*len(semantic_dis))-1 for x in list(np.arange(0, 1.1, 1.0/6))][1:]
visual_ts = np.array(sorted(visual_dis,reverse=True))[idx]    

edges_set_h = [[]for _ in range(hops_num)]
edges_set_v = [[]for _ in range(hops_num)]
edges_set_s = [[]for _ in range(hops_num)]

get_idx_s = lambda x:np.argwhere((x-semantic_ts)>=0)[0][0]
get_idx_v = lambda x:np.argwhere((x-visual_ts)>=0)[0][0]

for edge, h, s, v in zip(edges, hops, semantic_dis, visual_dis):
    h_idx = hops_map[h]
    s_idx = get_idx_s(s)
    v_idx = get_idx_v(v)

    edges_set_h[h_idx].append(edge)
    edges_set_s[s_idx].append(edge)
    edges_set_v[v_idx].append(edge)

for z in ['h', 's', 'v']:
    s = eval('edges_set_'+z)
    print('edges_set_'+z)
    for idx, e in enumerate(s):
        print(idx, len(e))

edges_set_h
0 21842
1 18638
2 18482
3 17086
4 15221
5 11924
edges_set_s
0 22222
1 12182
2 17192
3 17199
4 17199
5 17199
edges_set_v
0 21842
1 12555
2 17199
3 17199
4 17199
5 17199


In [400]:
sio.savemat('imagenet-aux-hier-graph.mat',{
    'edges_set_h':edges_set_h,
    'edges_set_s':edges_set_s,
    'edges_set_v':edges_set_v,
    'wnids':nodes,
    'descriptions':'split edges into six groups, train them with attention.'})

/home/zzc/anaconda3/envs/exp/lib/python3.7/site-packages/scipy/io/matlab/mio5.py:450: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  narr = np.asanyarray(source)


# 加入NELL的边

In [2]:
import scipy.io as sio
import json
# mat = sio.loadmat('imagenet-aux-21K-graph.mat')
# edges = mat['edges'].squeeze()
# hops = mat['hops'].squeeze()
# wnids = mat['wnids'].squeeze()
# semantic_dis = mat['semantic_dis'].squeeze()
# visual_dis = mat['visual_dis'].squeeze()

js = json.load(open('imagenet-dense-graph.json'))
edges = js['edges']
wnids = js['wnids']
vectors = js['vectors']
import pickle 
graph = pickle.load(open('/home/zzc/exp/zsl_code/zsl-gcn-pth/data/imagenet_graph.pkl','rb'),encoding='latin1') # nell graph

import json 
wordn = json.load(open('/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/invdict_wordn.json'))  # nell nodes
# for x in wordn:
#     if x not in wnids:
#         print(x)
# len(wordn)
# error1 = wordn.index('fa11misc')
# error2 = wordn.index('fall11')

nell_dict = {i:wnid for i,wnid in enumerate(wordn)}  # 32297
wordnet_dict = {wnid:i for i,wnid in enumerate(wnids)}  #32324

In [71]:
# 将nell中的结点id转换到imagenet的结点iddef 
def func(nell_id):
    try:
        name = nell_dict[nell_id]
        wnid = wordnet_dict[name]
    except:
        return -1
    return wnid

def check(x):
    if x in [error1,error2]:
        return -1
    xx = func(x)  
    if xx == -1:
        return -1
    return xx
n = len(wnids)
nell_edges = []
adjs_i = {x:[] for x in range(len(wnids))}
adjs_n = {x:[] for x in range(len(wnids))}
# 去重
for k, v in graph.items():
    a = check(k)
    if a == -1:
        continue
    v = list(set(v))
    for vv in v:
        b = check(vv)
        if b == -1:
            continue
        if a<b:
            adjs_n[a].append(b)
    adjs_n[a].append(a)
for k, v in edges:
    adjs_i[k].append(v)
    
# nell_edges = []
# for k, v in adjs.items():
#     for vv in v:
#         nell_edges.append([k, vv])

In [87]:
cnt=0
for k, v in adjs_n.items():
    cnt+=len(v)
cnt

64808

In [73]:
sum_edges =[]
for k, v in adjs_i.items():
    e = adjs_n[k]
    for ee in e:
        if ee not in v:
            adjs_i[k].append(ee)
cnt=0
for k, v in adjs_i.items():
    cnt+=len(v)
print('add', cnt-200082, 'edges.')
for k, v in adjs_i.items():
    for b in v:
        sum_edges.append([k, b])
print(len(sum_edges))

add 23441 edges.
223523


In [76]:
json.dump({
    'edges':sum_edges,
    'wnids':wnids,
    'vectors':vectors}
    , open('imagenet-dense-graph-nell.json', 'w'))

# sio.savemat('imagenet-plus-nell-edges.mat',{
#     'edges':sum_edges,
#     'hops':hops,
#     'semantic_dis':semantic_dis,
#     'visual_dis':visual_dis,
#     'wnids':wnids,
#     'aux_edges':np.array(nell_edges),
#     'descriptions':'32K nodes, word-net structure with nell relations.'})

In [226]:
import scipy.io as sio
mat = sio.loadmat('imagenet-aux-21K-graph.mat')
# mat = sio.loadmat('imagenet-multi-weight-graph-raw.mat')
edges = mat['edges'].squeeze()
hops = mat['hops'].squeeze()
wnids = mat['wnids'].squeeze()
semantic_dis = mat['semantic_dis'].squeeze()
visual_dis = mat['visual_dis'].squeeze()

n = len(wnids)-1
mask = []
for idx, (a, b) in enumerate(nell_edges):
    if not (a>n or b>n):
        mask.append(idx)
        
sio.savemat('imagenet-nell-edges-21K.mat',{
    'edges':edges,
    'hops':hops,
    'semantic_dis':semantic_dis,
    'visual_dis':visual_dis,
    'wnids':wnids,
    'aux_edges':np.array(nell_edges)[mask],
    'descriptions':'only 21K nodes, word-net structure with nell relations.'})



# 重跑nell结点关系的获取

In [94]:
import xml.etree.ElementTree as ET
import os
import pickle as pkl

srcfile = '/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/structure_released.xml'
tree = ET.parse(srcfile)
root = tree.getroot()  # root[0]:releaseData, root[1]:synset
start = root[1]

js = json.load(open('imagenet-dense-grouped-graph.json'))
wnids = js['wnids']
# ids_rev = {v:k for k,v in ids.items()}
wordnet_dict = {wnid:i for i,wnid in enumerate(wnids)}  #32324

def add_edge_dfs(node):
    edges = []
    vertice = [node.attrib["wnid"]]
    if len(node) == 0:
        return vertice, edges
    for child in node:
        if child.tag != "synset":
            print(child.tag)

        edges.append((node.attrib["wnid"], child.attrib["wnid"]))
        child_ver, child_edge = add_edge_dfs(child)
        edges.extend(child_edge)
        vertice.extend(child_ver)

    return vertice, edges

id_map = {wnid:i for i,wnid in enumerate(wnids)}  #32324
last = len(wnids)
id_map['fa11misc'] = last
id_map['fall11'] = last+1

adjs = {i:[] for i in range(len(id_map.keys()))}
nodes = [root[1]]
l = 0
save = None
while l < len(nodes):
    node = nodes[l]
    a = node.attrib["wnid"]
    a = id_map[a]
    adjs[a].append(a)
    for child in node:
        if child.tag != "synset":
            print(child.tag)
        b = id_map[child.attrib["wnid"]]
        adjs[a].append(b)
        if child not in nodes:
            nodes.append(child)
    l+=1


In [95]:
for k, v in adjs.items():
    adjs[k] = list(set(v))
edges = []
for a, b in adjs.items():
    for bb in b:
        edges.append([a, bb])
print(len(edges))

67169


In [96]:
sio.savemat('imagenet-nell-edges-all.mat', {
    'edges':np.array(edges),
    'wnids':list(id_map.keys()),
    'descriptions':'nell edges with direction'})

In [135]:
hier_edges = []
parallel_edges = []
self_edges =[] 
for k, v in adjs.items():
    self_edges.append([k, k])

    for vv in v:
        hier_edges.append([k, vv]) 
    v = sorted(v)
    for i in range(len(v)):
        for j in range(i+1, len(v)): 
            if i!=j and (v[i]>=1000 or v[j] >= 1000):
                parallel_edges.append([v[i], v[j]])


In [106]:
conver = lambda id:wordnet_dict[ids_rev[id]] 
mask1 = []
mask2 = []
mask3 = []
for idx, edge in enumerate(hier_edges):
    a, b = edge
    a, b = conver(a), conver(b)
    hier_edges[idx] = [a, b]
for idx, edge  in enumerate(parallel_edges):
    a, b = edge
    a, b = conver(a), conver(b)
    parallel_edges[idx] = [a, b]
for idx, edge  in enumerate(self_edges):
    a, b = edge
    a, b = conver(a), conver(b)
    self_edges[idx] = [a, b]

In [133]:
c = 0
mask = []
for idx, edge in enumerate(parallel_edges):
    a, b = edge
    if a < 1000 and b < 1000:
        continue
    mask.append(idx)
len(mask)

3218445

In [123]:
import scipy.io as sio
import numpy as np
sio.savemat('imagenet-graph-nell.mat', {
    'hier_edges':np.array(hier_edges),
    'wnids':wnids,
    'parallel_edges':np.array(parallel_edges)[mask],
    'self_edges':np.array(self_edges),
    'descriptions':'nell edges with hops'})
# edges_multi = sio.loadmat('imagenet-multi-weight-graph.mat')


In [42]:
hier_edges = []
parallel_edges = []
self_edges =[] 
for k, v in adjs_n.items():
    self_edges.append([k, k])
    if len(v) == 0:
        continue
    for vv in v:
        hier_edges.append([k, vv]) 
    v = sorted(v)
    for i in range(len(v)):
        for j in range(i, len(v)): 
            if i!=j:
                parallel_edges.append([v[i], v[j]])

mask1 = []
mask2 = []
mask3 = []
for idx, edge in enumerate(hier_edges):
    a, b = edge
    if a < len(wnids) and b < len(wnids):  
        mask1.append(idx)
for idx, edge  in enumerate(parallel_edges):
    a, b = edge
    if a < len(wnids) and b < len(wnids):  
        mask2.append(idx)
for idx, edge  in enumerate(self_edges):
    a, b = edge
    if a < len(wnids) and b < len(wnids):  
        mask3.append(idx)

In [47]:
import scipy.io as sio
import numpy as np
sio.savemat('imagenet-graph-nell.mat', {
    'hier_edges':np.array(hier_edges)[mask1],
    'wnids':wnids,
    'parallel_edges':np.array(parallel_edges)[mask2],
    'self_edges':np.array(self_edges)[mask3],
    'descriptions':'nell edges with hops'})
# edges_multi = sio.loadmat('imagenet-multi-weight-graph.mat')


In [34]:
import xml.etree.ElementTree as ET
import os
import pickle as pkl
from nltk.corpus import wordnet as wn
import json

def getnode(x):
    return wn.synset_from_pos_and_offset('n', int(x[1:]))


def getwnid(u):
    s = str(u.offset())
    return 'n' + (8 - len(s)) * '0' + s


srcfile = '/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/structure_released.xml'
tree = ET.parse(srcfile)
root = tree.getroot()  # root[0]:releaseData, root[1]:synset
start = root[1]
adjs = {}

js = json.load(open('imagenet-induced-graph.json'))
wnids = js['wnids']
id_map = {wnid:i for i,wnid in enumerate(wnids)}  #32324

id_map['fa11misc'] = len(wnids)
id_map['fall11'] = len(wnids)+1

# adjs = {i:[] for i in range(len(id_map.keys()))}
adjs = {i:[] for i in id_map.keys()}
node_depth = {i:0 for i in id_map.keys()}
def add_edge_dfs(node, d):
    wnid = node.attrib["wnid"]
    node_depth[node.attrib["wnid"]] = d
    if len(node) == 0:
        return 
    for child in node:
        if child.tag != "synset":
            print(child.tag)
        adjs[child.attrib["wnid"]].append(node.attrib["wnid"])
#         edges.append((node.attrib["wnid"], child.attrib["wnid"]))
        add_edge_dfs(child, d+1)
#         edges.extend(child_edge)
#         vertice.extend(child_ver)

#     return vertice, edges
for k, v in adjs.items():
    adjs[k] = list(set(v))
add_edge_dfs(start, 0)

In [5]:
# nell 层级
getname = lambda id: getnode(id).lemma_names()[0]
def find(node, d, path):
    if d == 0:
        for p in path[::-1]:
            pp = getname(p)
            print(p, pp+'->', end=' ')
        print('-'*12)
    else:
        for n in adjs[node]:
            if not n in ['fall11', 'fa11misc']:
                path.append(n)
                find(n, d-1, path)
                path.pop()
for k, v in node_depth.items():
    if v == 12:
        find(k, v, [])
        
        

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n

...

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-to

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-to

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-to

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02414578 wild_sheep-> n02415435 mountain_sheep-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806

KeyboardInterrupt: 

In [13]:
js = json.load(open('imagenet-induced-graph.json'))
wnids = js['wnids']
edges = js['edges']
adjs = {i:[] for i in range(len(wnids))} 
for a,b in edges:
    adjs[b].append(a)

In [14]:
from collections import Counter
depth = {i:0 for i in adjs.keys()}
# 循环多次直至深度不再更新
for _ in range(10):
    for k,v in adjs.items():
        for vv in v:
            depth[vv] = max(depth[k]+1, depth[vv])
    print(Counter(depth.values()))

Counter({1: 12459, 2: 8970, 3: 5100, 4: 3202, 5: 1714, 6: 450, 0: 309, 7: 93, 8: 16, 9: 10, 10: 1})
Counter({3: 8209, 4: 8079, 2: 5884, 5: 5762, 6: 2450, 1: 882, 7: 571, 0: 309, 8: 148, 9: 29, 10: 1})
Counter({4: 8014, 5: 7731, 6: 4964, 3: 4914, 7: 2217, 2: 2143, 1: 882, 8: 789, 0: 309, 9: 213, 10: 123, 11: 25})
Counter({5: 6970, 4: 6415, 6: 5471, 3: 3891, 7: 3198, 2: 2143, 8: 1721, 1: 882, 9: 789, 0: 309, 10: 302, 11: 194, 12: 38, 13: 1})
Counter({5: 6662, 4: 6274, 6: 5220, 3: 3891, 7: 3093, 2: 2143, 8: 1831, 9: 1002, 1: 882, 10: 547, 11: 347, 0: 309, 12: 108, 13: 14, 14: 1})
Counter({5: 6643, 4: 6274, 6: 5146, 3: 3891, 7: 3041, 2: 2143, 8: 1750, 9: 1011, 1: 882, 10: 564, 11: 458, 0: 309, 12: 191, 13: 20, 14: 1})
Counter({5: 6643, 4: 6274, 6: 5146, 3: 3891, 7: 3027, 2: 2143, 8: 1745, 9: 999, 1: 882, 10: 544, 11: 472, 0: 309, 12: 207, 13: 41, 14: 1})
Counter({5: 6643, 4: 6274, 6: 5146, 3: 3891, 7: 3027, 2: 2143, 8: 1745, 9: 999, 1: 882, 10: 544, 11: 467, 0: 309, 12: 212, 13: 41, 14: 1}

In [27]:
idx = wnids.index('n01468238')
a = adjs[idx]
for aa in a:
    print(wnids[aa], getname(wnids[aa]))

n01469723 salp
n01470145 doliolum
n01470479 larvacean
n01470733 appendicularia
n01468712 ascidian


1310

In [16]:
# nell 层级
adjs_r = {i:[] for i in range(len(wnids))} 
for a,b in edges:
    adjs_r[a].append(b)
    
getname = lambda id: getnode(id).lemma_names()[0]
def find(node, d, path):
    if d == 0:
        for p in path[::-1]:
            pp = getname(wnids[p])
            print(wnids[p], pp+'->', end=' ')
        print('-'*12)
    else:
        for n in adjs_r[node]:
            path.append(n)
            find(n, d-1, path)
            path.pop()
            
for k, v in depth.items():
    if v > 10:
        #print(k,wnids[k],getname(wnids[k]), adjs_r[k])
        find(k, v, [])
        

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n01438208 cypriniform_fish-> n01439121 cyprinid-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n01438208 cypriniform_fish-> n01439121 cyprinid-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01503061 bird-> n01844917 aquatic_bird-> n01845132 waterfowl-> n01845477 anseriform_bird-> n01846331 duck-> n01852861 sea_duck-> n01854415 merganser-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02062017 aquatic_mammal-> n02062430 cetacean-> n02062744 whale-> n02066707 toothed_

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n02098550 sporting_dog-> n02100399 setter-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n02098550 sporting_dog-> n02100399 setter-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n02098550 sporting_dog-> n02100399 setter-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n0209

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02642107 scorpaenoid-> n02642644 scorpaenid-> ------------
n00021939 artifact-> n03575240 instrumentality-> n03183080 device-> n03574816 instrument-> n04565375 weapon-> n03467984 gun-> n03343853 firearm-> n02759963 autoloader-> n02760429 automatic_firearm-> n03701391 machine_gun-> n02760855 automatic_rifle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n02098550 sporting_dog-> n02101108 spaniel-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n0240

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02419796 antelope-> n02423022 gazelle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02062017 aquatic_mammal-> n02075927 pinniped_mammal-> n02076196 seal-> n02076779 eared_seal-> n02077923 sea_lion-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02083346 canine-> n02084071 dog-> n02087122 hunting_dog-> n02098550 sporting_dog-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n01438208 cypriniform_fi

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02407959 Old_World_buffalo-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02402010 bovine-> n02402425 cattle-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n02534559 salmonid-> n02534734 salmon-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid

...

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02652668 plectognath-> n02653786 filefish-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02642107 scorpaenoid-> n02650050 gurnard-> n02650541 sea_robin-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02623445 scombroid-> n02624167 mackerel-> n02625612 Spanish_mackerel-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02632989 butterfish-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01503061 bird-> n01844917 aquatic_bird-> n01845132 waterfowl-> n01845477 anseriform_bird-> n01846331 duck-> n01852861 sea_duck-> n01853498 scoter-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02565573 bass-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n02521646 ga

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02430045 deer-> n02433925 caribou-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02394477 even-toed_ungulate-> n02399000 ruminant-> n02401031 bovid-> n02416519 goat-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02373336 odd-toed_ungulate-> n02374149 equine-> n02374451 horse-> n02381460 wild_horse-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02373336 odd-toed_ungulate-> n02374149 equine-> n02374451 horse-> n02377703 saddle_horse-> ------------
n00004

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02373336 odd-toed_ungulate-> n02374149 equine-> n02374451 horse-> n02386310 workhorse-> n02386496 draft_horse-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02370806 ungulate-> n02373336 odd-toed_ungulate-> n02374149 equine-> n02374451 horse-> n02382948 racehorse-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01861778 mammal-> n01886756 placental-> n02075296 carnivore-> n02120997 feline-> n02121620 cat-> n02121808 domestic_cat-> n02122725 tom-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n01428580 soft-finned_fish-> n01438208 cypriniform_fish-> n014447

n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02610980 threadfin-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02612657 blennioid_fish-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n02528163 teleost_fish-> n02552171 spiny-finned_fish-> n02554730 percoid_fish-> n02612657 blennioid_fish-> n02615642 prickleback-> ------------
n00004475 organism-> n00015388 animal-> n01466257 chordate-> n01471682 vertebrate-> n01473806 aquatic_vertebrate-> n02512053 fish-> n02514825 bony_fish-> n0252

In [91]:
for k, v in depth.items():
    if v == 0:
        print(k,wnids[k],getname(wnids[k]))

920 n06874185 traffic_light
1263 n06793231 sign
1682 n07707451 vegetable
1708 n09287968 geological_formation
2589 n05235879 rib
2602 n06470073 document
2606 n07942152 people
2624 n13900287 toroid
2685 n04124488 saddlery
2700 n08182379 crowd
2732 n09282208 floor
2737 n13917785 truncated_cone
2832 n08658309 soil_horizon
2855 n05314075 canthus
2869 n08571275 midfield
2899 n09433839 shoreline
2912 n02749953 assembly
2930 n13862780 figure
2935 n03260206 dye-works
2958 n05418717 vein
2964 n08614632 fairground
2966 n09450163 sun
2983 n08679562 continental_divide
2991 n08611421 no-parking_zone
3001 n09247410 cloud
3007 n08628141 kasbah
3014 n13873917 circle
3032 n08623676 locus_of_infection
3045 n03992436 potsherd
3114 n14915184 ice
3116 n08555710 crawlspace
3134 n00120010 hop
3191 n03963645 playground
3260 n02764398 ax_handle
3296 n13867492 amorphous_shape
3313 n08539276 outskirts
3344 n08679269 low-water_mark
3374 n14974264 paper
3384 n04611351 yardarm
3393 n03817331 negative_magnetic_pole
3

# 为原图增添层级
    # 当邻居节点来自于更高层，其类内图更杂，学习到的分类器应更具泛化性；更底层，则更具体。

In [28]:
import scipy.io as sio
import json
import pickle 

from nltk.corpus import wordnet as wn

def getnode(x):
    return wn.synset_from_pos_and_offset('n', int(x[1:]))

base_graph = json.load(open('imagenet-induced-graph.json')) # 由下指向上
wnids = base_graph['wnids']
# graph = pickle.load(open('/home/zzc/exp/zsl_code/zsl-gcn-pth/data/imagenet_graph.pkl','rb'),encoding='latin1') # nell graph
wordn = json.load(open('/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/invdict_wordn.json'))  # nell nodes

nell_dict = {i:wnid for i,wnid in enumerate(wordn)}  # 32297

id_map = {wnid:i for i,wnid in enumerate(wnids)}  #32324
id_map['fa11misc'] = len(wnids)  # 杂类
id_map['fall11'] = len(wnids)+1  # 根节点


In [30]:
import xml.etree.ElementTree as ET
import os
import pickle as pkl
srcfile = '/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/structure_released.xml'
tree = ET.parse(srcfile)
root = tree.getroot()  # root[0]:releaseData, root[1]:synset
start = root[1]
nell_graph = {}
def add_edge_dfs(node):
    edges = []
    vertice = node.attrib["wnid"]
    if not nell_graph.__contains__(vertice):
        nell_graph[vertice] = []
    if len(node) == 0:
        return 
    for child in node:
        if child.tag != "synset":
            print(child.tag)
        nell_graph[vertice].append(child.attrib["wnid"])
        add_edge_dfs(child)
    return 
add_edge_dfs(start)


In [6]:
# 统计fa11misc中有多少个结点在其他处也有
target = nell_graph['fa11misc']
record = {t:0 for t in target}
cnt = 0
for k,v in nell_graph.items():
    for vv in v:
        if vv in target and k != 'fa11misc':
            cnt+=1
            record[vv] = 1
            print(k, getnode(k).lemma_names()[0], vv, getnode(vv).lemma_names()[0])
            
# 删去重复边
save = []
for k, v in record.items():
    if v == 0:
        save.append(k)
nell_graph['fa11misc'] = save


n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 K

n07721456 chili n07721678 jalapeno
n07721456 chili n07721942 cayenne
n07721325 hot_pepper n07722052 tabasco
n07721325 hot_pepper n07721456 chili
n07721325 hot_pepper n07722052 tabasco
n07721325 hot_pepper n07721456 chili
n07721325 hot_pepper n07722052 tabasco
n07721325 hot_pepper n07721456 chili
n07721325 hot_pepper n07722052 tabasco
n07721325 hot_pepper n07721456 chili
n07720442 pepper n07720615 sweet_pepper
n07720442 pepper n07721325 hot_pepper
n07720442 pepper n07720615 sweet_pepper
n07720442 pepper n07721325 hot_pepper
n07720442 pepper n07720615 sweet_pepper
n07720442 pepper n07721325 hot_pepper
n07734292 cherry_tomato n07734417 plum_tomato
n07734292 cherry_tomato n07734417 plum_tomato
n07734292 cherry_tomato n07734417 plum_tomato
n07734292 cherry_tomato n07734417 plum_tomato
n07734017 tomato n07734183 beefsteak_tomato
n07734017 tomato n07734292 cherry_tomato
n07734017 tomato n07734183 beefsteak_tomato
n07734017 tomato n07734292 cherry_tomato
n07734017 tomato n07734183 beefsteak_to

n07679356 bread n07686461 salt-rising_bread
n07679356 bread n07682477 English_muffin
n07679356 bread n07680313 bap
n07679356 bread n07684289 nan
n07679356 bread n07686873 toast
n07679356 bread n07683138 Host
n07679356 bread n07684517 raisin_bread
n07679356 bread n07681355 caraway_seed_bread
n07679356 bread n07681926 cracker
n07679356 bread n07682624 flatbread
n07679356 bread n07682197 crouton
n07679356 bread n07680517 breadstick
n07679356 bread n07686634 simnel
n07679356 bread n07680416 barmbrack
n07679356 bread n07680168 anadama_bread
n07679356 bread n07685730 rye_bread
n07679356 bread n07681805 cracked-wheat_bread
n07679356 bread n07681691 cinnamon_bread
n07679356 bread n07684600 quick_bread
n07679356 bread n07686720 sour_bread
n07679356 bread n07680761 brown_bread
n07679356 bread n07681450 challah
n07679356 bread n07684164 matzo
n07679356 bread n07680932 bun
n07679356 bread n07682952 gluten_bread
n07679356 bread n07687053 wafer
n07679356 bread n07684422 onion_bread
n07679356 bread n

n07684600 quick_bread n07685118 date-nut_bread
n07684600 quick_bread n07685303 oatcake
n07684600 quick_bread n07693972 biscuit
n07684600 quick_bread n07685546 skillet_bread
n07684600 quick_bread n07687789 cornbread
n07684600 quick_bread n07690273 muffin
n07684600 quick_bread n07690892 scone
n07684600 quick_bread n07690585 Yorkshire_pudding
n07684600 quick_bread n07685218 nut_bread
n07684600 quick_bread n07684938 banana_bread
n07693972 biscuit n07694169 rolled_biscuit
n07693972 biscuit n07694403 baking-powder_biscuit
n07693972 biscuit n07694839 hardtack
n07693972 biscuit n07694516 buttermilk_biscuit
n07693972 biscuit n07694169 rolled_biscuit
n07693972 biscuit n07694403 baking-powder_biscuit
n07693972 biscuit n07694839 hardtack
n07693972 biscuit n07694516 buttermilk_biscuit
n07693972 biscuit n07694169 rolled_biscuit
n07693972 biscuit n07694403 baking-powder_biscuit
n07693972 biscuit n07694839 hardtack
n07693972 biscuit n07694516 buttermilk_biscuit
n07693972 biscuit n07694169 rolled_biscu

n07809368 flavorer n07827750 poppy_seed
n07809368 flavorer n07823814 curry_powder
n07809368 flavorer n07826544 almond_extract
n07809368 flavorer n07814925 ginger
n07809368 flavorer n07810531 bouillon_cube
n07809368 flavorer n07774479 cola_extract
n07809368 flavorer n07819769 nasturtium
n07809368 flavorer n07818029 fennel_seed
n07809368 flavorer n07921090 cassareep
n07809368 flavorer n07818277 garlic
n07809368 flavorer n07858595 sweetening
n07809368 flavorer n07815588 pepper
n07809368 flavorer n07812662 spearmint_oil
n07809368 flavorer n07818133 fenugreek
n07809368 flavorer n07828275 lemon_extract
n07809368 flavorer n07822323 cardamom
n07809368 flavorer n07812913 wintergreen_oil
n07809368 flavorer n07822518 cayenne
n07809368 flavorer n07828156 celery_seed
n07809368 flavorer n07822687 chili_powder
n07809368 flavorer n07821919 turmeric
n07809368 flavorer n07810907 condiment
n07809368 flavorer n07817465 coriander
n07809368 flavorer n07920989 mocha
n07809368 flavorer n07827554 caraway_seed


...

n07892813 white_wine n07896765 Moselle
n07892813 white_wine n07894451 Canary_wine
n07892813 white_wine n07894551 Chablis
n07892813 white_wine n07896893 Muscadet
n07892813 white_wine n07898443 Sauterne
n07892813 white_wine n07897975 sack
n07892813 white_wine n07899769 Vouvray
n07892813 white_wine n07898247 Soave
n07892813 white_wine n07899533 Chenin_blanc
n07892813 white_wine n07895100 Pinot_blanc
n07892813 white_wine n07897200 Rhine_wine
n07892813 white_wine n07894703 Montrachet
n07892813 white_wine n07899660 Verdicchio
n07892813 white_wine n07895962 Sauvignon_blanc
n07892813 white_wine n07894799 Chardonnay
n07892813 white_wine n07899899 Yquem
n07892813 white_wine n07896765 Moselle
n07892813 white_wine n07894451 Canary_wine
n07892813 white_wine n07894551 Chablis
n07892813 white_wine n07896893 Muscadet
n07892813 white_wine n07898443 Sauterne
n07892813 white_wine n07897975 sack
n07892813 white_wine n07899769 Vouvray
n07892813 white_wine n07898247 Soave
n07892813 white_wine n07899533 Chen

n07912211 highball n07913882 collins
n07912211 highball n07917618 sling
n07912211 highball n07915491 julep
n07912211 highball n07915094 gin_and_tonic
n07912211 highball n07913774 cobbler
n07912211 highball n07917507 Scotch_and_soda
n07912211 highball n07919165 zombie
n07912211 highball n07913882 collins
n07912211 highball n07917618 sling
n07912211 highball n07915491 julep
n07912211 highball n07915094 gin_and_tonic
n07912211 highball n07913774 cobbler
n07912211 highball n07917507 Scotch_and_soda
n07912211 highball n07919165 zombie
n07912211 highball n07913882 collins
n07912211 highball n07917618 sling
n07912211 highball n07915491 julep
n07912211 highball n07915094 gin_and_tonic
n07912211 highball n07913774 cobbler
n07912211 highball n07917507 Scotch_and_soda
n07912211 highball n07919165 zombie
n07912211 highball n07913882 collins
n07912211 highball n07917618 sling
n07912211 highball n07915491 julep
n07912211 highball n07915094 gin_and_tonic
n07912211 highball n07913774 cobbler
n07912211

n01366276 corynebacterium n01366700 Corynebacterium_diphtheriae
n01366276 corynebacterium n01366700 Corynebacterium_diphtheriae
n01366276 corynebacterium n01366700 Corynebacterium_diphtheriae
n01366276 corynebacterium n01366700 Corynebacterium_diphtheriae
n01366276 corynebacterium n01366700 Corynebacterium_diphtheriae
n01375204 actinomycete n01376237 streptomyces
n01375204 actinomycete n01376237 streptomyces
n01375204 actinomycete n01376237 streptomyces
n01375204 actinomycete n01376237 streptomyces
n01375204 actinomycete n01376237 streptomyces
n01375204 actinomycete n01376237 streptomyces
n01376237 streptomyces n01376437 Streptomyces_erythreus
n01376237 streptomyces n01376543 Streptomyces_griseus
n01376237 streptomyces n01376437 Streptomyces_erythreus
n01376237 streptomyces n01376543 Streptomyces_griseus
n01376237 streptomyces n01376437 Streptomyces_erythreus
n01376237 streptomyces n01376543 Streptomyces_griseus
n01376237 streptomyces n01376437 Streptomyces_erythreus
n01376237 streptom

n13872975 conic_section n13878306 ellipse
n13872975 conic_section n13878306 ellipse
n13866144 polygon n13866626 convex_polygon
n13866144 polygon n13882487 heptagon
n13866144 polygon n13882563 octagon
n13866144 polygon n13882276 hexagon
n13866144 polygon n13882713 decagon
n13866144 polygon n13882639 nonagon
n13866144 polygon n13879320 triangle
n13866144 polygon n13882201 pentagon
n13866144 polygon n13883603 spherical_polygon
n13866144 polygon n13866827 concave_polygon
n13866144 polygon n13866626 convex_polygon
n13866144 polygon n13882487 heptagon
n13866144 polygon n13882563 octagon
n13866144 polygon n13882276 hexagon
n13866144 polygon n13882713 decagon
n13866144 polygon n13882639 nonagon
n13866144 polygon n13879320 triangle
n13866144 polygon n13882201 pentagon
n13866144 polygon n13883603 spherical_polygon
n13866144 polygon n13866827 concave_polygon
n13866144 polygon n13866626 convex_polygon
n13866144 polygon n13882487 heptagon
n13866144 polygon n13882563 octagon
n13866144 polygon n13882

n13869991 straight_line n13871717 diameter
n13877408 element n13877667 element_of_a_cylinder
n13877408 element n13877547 element_of_a_cone
n04960277 black n04960582 coal_black
n13862780 figure n13863186 plane_figure
n13862780 figure n13863020 pencil
n13862780 figure n13880994 parallel
n13862780 figure n13862552 equilateral
n13862780 figure n13863473 solid_figure
n13913849 branch n13914265 fork
n13913849 branch n13914141 brachium
n13897377 flank n13897528 hypotenuse
n04968895 blue n04969540 steel_blue
n04968895 blue n04974859 ultramarine
n04968895 blue n04969242 azure
n04968895 blue n04969798 greenish_blue
n04968895 blue n04969952 purplish_blue
n04968895 blue n04969540 steel_blue
n04968895 blue n04974859 ultramarine
n04968895 blue n04969242 azure
n04968895 blue n04969798 greenish_blue
n04968895 blue n04969952 purplish_blue
n01384687 parasite n01385330 ectoparasite
n01384687 parasite n01385017 endoparasite
n01384687 parasite n01385330 ectoparasite
n01384687 parasite n01385017 endoparasit

In [33]:
for k,v in nell_graph.items():
    nell_graph[k].append(k)

In [93]:
# 统计图上结点深度,添加边

from collections import Counter
depth = {i:0 for i in nell_graph.keys()}
# 循环多次直至深度不再更新
for _ in range(10):
    for k,v in nell_graph.items():
        for vv in v:
            if vv != k:
                depth[vv] = max(depth[k]+1, depth[vv])
    print(Counter(depth.values()))


Counter({5: 7093, 6: 6196, 4: 5383, 7: 4302, 3: 3067, 8: 2473, 9: 1274, 2: 1090, 10: 586, 11: 383, 1: 286, 12: 163, 0: 1})
Counter({6: 6422, 7: 6160, 5: 4886, 8: 3897, 4: 3089, 9: 2355, 3: 1601, 10: 1412, 11: 934, 2: 521, 12: 502, 13: 356, 14: 156, 1: 5, 0: 1})
Counter({6: 6352, 7: 6051, 5: 4909, 8: 4090, 4: 3007, 9: 2424, 3: 1591, 10: 1384, 11: 868, 12: 517, 13: 457, 2: 418, 14: 212, 15: 10, 1: 5, 0: 1, 16: 1})
Counter({6: 6384, 7: 6057, 5: 4907, 8: 4093, 4: 3019, 9: 2424, 3: 1540, 10: 1384, 11: 868, 12: 517, 13: 457, 2: 418, 14: 212, 15: 10, 1: 5, 0: 1, 16: 1})
Counter({6: 6384, 7: 6065, 5: 4917, 8: 4094, 4: 3000, 9: 2424, 3: 1540, 10: 1384, 11: 868, 12: 517, 13: 457, 2: 418, 14: 212, 15: 10, 1: 5, 0: 1, 16: 1})
Counter({6: 6385, 7: 6065, 5: 4906, 8: 4104, 4: 3000, 9: 2424, 3: 1540, 10: 1384, 11: 868, 12: 517, 13: 457, 2: 418, 14: 212, 15: 10, 1: 5, 0: 1, 16: 1})
Counter({6: 6384, 7: 6065, 5: 4906, 8: 4104, 4: 3000, 9: 2425, 3: 1540, 10: 1384, 11: 868, 12: 517, 13: 457, 2: 418, 14: 2

In [108]:
for k, v in depth.items():
    if v == 1:
        if not k in ['fa11misc','fall11']:
            print(k, getnode(k).lemma_names()[0])

n09287968 geological_formation
n00019128 natural_object
n00523513 sport
n00021939 artifact


In [151]:
len(list(nell_graph.keys()))

32297

In [98]:
import numpy as np
layers = np.unique(list(depth.values()))
edges_set_a = [[] for _ in range(len(layers))]
edges_set_r = [[] for _ in range(len(layers))]
for k, v in nell_graph.items():
    d_k = depth[k]
    k = id_map[k]
    for vv in v:
        d_v = depth[vv]
        vv = id_map[vv]
        edges_set_a[d_v].append([k, vv])  # 上-》下
        edges_set_r[d_k].append([vv, k])  # 下-》上

In [152]:
id_map.keys()

dict_keys(['n01440764', 'n01443537', 'n01484850', 'n01491361', 'n01494475', 'n01496331', 'n01498041', 'n01514668', 'n01514859', 'n01518878', 'n01530575', 'n01531178', 'n01532829', 'n01534433', 'n01537544', 'n01558993', 'n01560419', 'n01580077', 'n01582220', 'n01592084', 'n01601694', 'n01608432', 'n01614925', 'n01616318', 'n01622779', 'n01629819', 'n01630670', 'n01631663', 'n01632458', 'n01632777', 'n01641577', 'n01644373', 'n01644900', 'n01664065', 'n01665541', 'n01667114', 'n01667778', 'n01669191', 'n01675722', 'n01677366', 'n01682714', 'n01685808', 'n01687978', 'n01688243', 'n01689811', 'n01692333', 'n01693334', 'n01694178', 'n01695060', 'n01697457', 'n01698640', 'n01704323', 'n01728572', 'n01728920', 'n01729322', 'n01729977', 'n01734418', 'n01735189', 'n01737021', 'n01739381', 'n01740131', 'n01742172', 'n01744401', 'n01748264', 'n01749939', 'n01751748', 'n01753488', 'n01755581', 'n01756291', 'n01768244', 'n01770081', 'n01770393', 'n01773157', 'n01773549', 'n01773797', 'n01774384', '

In [100]:
import numpy as np
layers = np.unique(list(depth.values()))
edges_set_a = [[] for _ in range(len(layers))]
edges_set_r = [[] for _ in range(len(layers))]

for k, v in nell_graph.items():
    d_k = depth[k]
    k = id_map[k]
    for vv in v:
        d_v = depth[vv]
        vv = id_map[vv]
        edges_set_a[d_v].append([k, vv])  # 上-》下
        edges_set_r[d_k].append([vv, k])  # 下-》上

In [18]:
inf_y = []
model.eval()
for i in range(edges.shape[0]):
    x = get_input(edges[i], hops[i], semantic_dis[i])
    y = visual_dis[0][i]
    if y == -1.0:
        pred = model(torch.tensor(x).float().cuda()).cpu().tolist()[0]
        inf_y.append(pred)
    else:
        inf_y.append(y)
visual_dis_pred = scaler.fit_transform(np.vstack(inf_y))
visual_dis_pred = 1-visual_dis_pred

10
1406
6265
13337
18057
18850
14644
9247
5106
2462
1064
582
163


91193

In [40]:
sio.savemat('directed-hierarchy-nell-graph.mat', {
    'edges':[edges_set_a_, edges_set_r_],
    'wnids':list(id_map.keys()),
    'descriptions':'construct nell graph with direction and hierarchy'})
# edges_multi = sio.loadmat('imagenet-multi-weight-graph.ma

In [155]:
from collections import Counter
import numpy as np
roots = np.argwhere(np.array(_in)==0).squeeze()
for n in roots:
    print(wnids[n], getnode(wnids[n]).lemma_names()[0])

n06874185 traffic_light
n06793231 sign
n07707451 vegetable
n09287968 geological_formation
n05235879 rib
n06470073 document
n07942152 people
n13900287 toroid
n04124488 saddlery
n08182379 crowd
n09282208 floor
n13917785 truncated_cone
n08658309 soil_horizon
n05314075 canthus
n08571275 midfield
n09433839 shoreline
n02749953 assembly
n13862780 figure
n03260206 dye-works
n05418717 vein
n08614632 fairground
n09450163 sun
n08679562 continental_divide
n08611421 no-parking_zone
n09247410 cloud
n08628141 kasbah
n13873917 circle
n08623676 locus_of_infection
n03992436 potsherd
n14915184 ice
n08555710 crawlspace
n00120010 hop
n03963645 playground
n02764398 ax_handle
n13867492 amorphous_shape
n08539276 outskirts
n08679269 low-water_mark
n14974264 paper
n04611351 yardarm
n03817331 negative_magnetic_pole
n09392402 pinetum
n03573848 insole
n09209025 asthenosphere
n08663051 three-mile_limit
n03474896 haft
n04979307 cryptic_coloration
n04515729 upstairs
n08674344 subtropics
n08540532 borough
n08569482 fa

IndexError: list index out of range

In [146]:
nodes = nell_graph['fall11']
for n in nodes[:-1]:
    print(n, getnode(n).lemma_names()[0])
    
for k,v in nell_graph.items():
    for vv in v:
        if vv in nodes and k != 'fall11':
            print(k, getnode(k).lemma_names()[0], vv, getnode(vv).lemma_names()[0])

n00017222 plant
n09287968 geological_formation
n00019128 natural_object
n00523513 sport
n00021939 artifact
n12992868 fungus
n00007846 person
n00015388 animal
n00004475 organism n00017222 plant
n00004475 organism n12992868 fungus
n00004475 organism n00007846 person
n00004475 organism n00015388 animal


In [141]:
# 统计fa11misc中有多少个结点在其他处也有
target = nell_graph['fa11misc']
record = {t:0 for t in target}
cnt = 0
for k,v in nell_graph.items():
    for vv in v:
        if vv in target and k != 'fa11misc':
            cnt+=1
            record[vv] = 1
            print(k, getnode(k).lemma_names()[0], vv, getnode(vv).lemma_names()[0])

n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 Kentucky_wonder
n07727868 green_bean n07728391 scarlet_runner
n07727868 green_bean n07728585 haricot_vert
n07727868 green_bean n07728053 snap_bean
n07727868 green_bean n07728181 string_bean
n07727868 green_bean n07728284 K

n07710616 potato n07711232 home_fries
n07710616 potato n07711569 mashed_potato
n07710616 potato n07711799 Uruguay_potato
n07710616 potato n07710952 baked_potato
n07710616 potato n07711080 french_fries
n07710616 potato n07711232 home_fries
n07710616 potato n07711569 mashed_potato
n07710616 potato n07711799 Uruguay_potato
n07720615 sweet_pepper n07720875 bell_pepper
n07720615 sweet_pepper n07721018 green_pepper
n07720615 sweet_pepper n07721118 globe_pepper
n07720615 sweet_pepper n07721195 pimento
n07720615 sweet_pepper n07720875 bell_pepper
n07720615 sweet_pepper n07721018 green_pepper
n07720615 sweet_pepper n07721118 globe_pepper
n07720615 sweet_pepper n07721195 pimento
n07720615 sweet_pepper n07720875 bell_pepper
n07720615 sweet_pepper n07721018 green_pepper
n07720615 sweet_pepper n07721118 globe_pepper
n07720615 sweet_pepper n07721195 pimento
n07720615 sweet_pepper n07720875 bell_pepper
n07720615 sweet_pepper n07721018 green_pepper
n07720615 sweet_pepper n07721118 globe_pepper
n077206

n07572957 canned_food n07573103 canned_meat
n07572957 canned_food n07573103 canned_meat
n07573103 canned_meat n07573347 Spam
n07573103 canned_meat n07573347 Spam
n07573103 canned_meat n07573347 Spam
n07573103 canned_meat n07573347 Spam
n07566863 starches n07710616 potato
n07566863 starches n07679356 bread
n07566863 starches n07804323 rice
n07566863 starches n07710616 potato
n07566863 starches n07679356 bread
n07566863 starches n07804323 rice
n07566863 starches n07710616 potato
n07566863 starches n07679356 bread
n07566863 starches n07804323 rice
n07679356 bread n07687053 wafer
n07679356 bread n07684422 onion_bread
n07679356 bread n07682808 garlic_bread
n07679356 bread n07682316 dark_bread
n07679356 bread n07683786 loaf_of_bread
n07679356 bread n07687211 white_bread
n07679356 bread n07686461 salt-rising_bread
n07679356 bread n07682477 English_muffin
n07679356 bread n07680313 bap
n07679356 bread n07684289 nan
n07679356 bread n07686873 toast
n07679356 bread n07683138 Host
n07679356 bread n

n07684600 quick_bread n07690273 muffin
n07684600 quick_bread n07690892 scone
n07684600 quick_bread n07690585 Yorkshire_pudding
n07684600 quick_bread n07685218 nut_bread
n07684600 quick_bread n07684938 banana_bread
n07684600 quick_bread n07685031 date_bread
n07684600 quick_bread n07685399 Irish_soda_bread
n07684600 quick_bread n07685118 date-nut_bread
n07684600 quick_bread n07685303 oatcake
n07684600 quick_bread n07693972 biscuit
n07684600 quick_bread n07685546 skillet_bread
n07684600 quick_bread n07687789 cornbread
n07684600 quick_bread n07690273 muffin
n07684600 quick_bread n07690892 scone
n07684600 quick_bread n07690585 Yorkshire_pudding
n07684600 quick_bread n07685218 nut_bread
n07684600 quick_bread n07684938 banana_bread
n07684600 quick_bread n07685031 date_bread
n07684600 quick_bread n07685399 Irish_soda_bread
n07684600 quick_bread n07685118 date-nut_bread
n07684600 quick_bread n07685303 oatcake
n07684600 quick_bread n07693972 biscuit
n07684600 quick_bread n07685546 skillet_bread


n07809096 ingredient n07926540 malted_milk
n07809368 flavorer n07828642 vanilla_bean
n07809368 flavorer n07826453 angelica
n07809368 flavorer n07818572 garlic_chive
n07809368 flavorer n07813495 onion_salt
n07809368 flavorer n07827130 juniper_berries
n07809368 flavorer n07828378 monosodium_glutamate
n07809368 flavorer n07812184 spice
n07809368 flavorer n07783827 anchovy_paste
n07809368 flavorer n07824702 paprika
n07809368 flavorer n07828041 dill_seed
n07809368 flavorer n07812790 lemon_oil
n07809368 flavorer n07819303 mustard_seed
n07809368 flavorer n07813579 seasoned_salt
n07809368 flavorer n07813107 salt
n07809368 flavorer n07813324 celery_salt
n07809368 flavorer n07826653 anise
n07809368 flavorer n07827284 saffron
n07809368 flavorer n07816052 sassafras
n07809368 flavorer n07827750 poppy_seed
n07809368 flavorer n07823814 curry_powder
n07809368 flavorer n07826544 almond_extract
n07809368 flavorer n07814925 ginger
n07809368 flavorer n07810531 bouillon_cube
n07809368 flavorer n07774479 co

...

n07892813 white_wine n07896893 Muscadet
n07892813 white_wine n07898443 Sauterne
n07892813 white_wine n07897975 sack
n07892813 white_wine n07899769 Vouvray
n07892813 white_wine n07898247 Soave
n07892813 white_wine n07899533 Chenin_blanc
n07892813 white_wine n07895100 Pinot_blanc
n07892813 white_wine n07897200 Rhine_wine
n07892813 white_wine n07894703 Montrachet
n07892813 white_wine n07899660 Verdicchio
n07892813 white_wine n07895962 Sauvignon_blanc
n07892813 white_wine n07894799 Chardonnay
n07892813 white_wine n07899899 Yquem
n07892813 white_wine n07896765 Moselle
n07892813 white_wine n07894451 Canary_wine
n07897200 Rhine_wine n07897438 Riesling
n07897200 Rhine_wine n07897600 liebfraumilch
n07897200 Rhine_wine n07897438 Riesling
n07897200 Rhine_wine n07897600 liebfraumilch
n07897200 Rhine_wine n07897438 Riesling
n07897200 Rhine_wine n07897600 liebfraumilch
n07897200 Rhine_wine n07897438 Riesling
n07897200 Rhine_wine n07897600 liebfraumilch
n07897200 Rhine_wine n07897438 Riesling
n078972

n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07917618 sling n07917951 rum_sling
n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07917618 sling n07917951 rum_sling
n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07917618 sling n07917951 rum_sling
n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07917618 sling n07917951 rum_sling
n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07917618 sling n07917951 rum_sling
n07917618 sling n07917874 gin_sling
n07917618 sling n07917791 brandy_sling
n07911677 cocktail n07916041 martini
n07911677 cocktail n07917392 sidecar
n07911677 cocktail n07915918 margarita
n07911677 cocktail n07915366 Harvey_Wallbanger
n07911677 cocktail n07931612 White_Russian
n07911677 cocktail n07913393 Bloody_Mary
n07911677 cocktail n07916437 old_fashioned
n07911677 cocktail n07914413 daiquiri
n07911677 cocktail n07916582 pink_lady
n07911

n01402600 brown_algae n01404365 fucoid
n01402600 brown_algae n01403457 kelp
n01402600 brown_algae n01404365 fucoid
n01402600 brown_algae n01403457 kelp
n01402600 brown_algae n01404365 fucoid
n01402600 brown_algae n01403457 kelp
n01402600 brown_algae n01404365 fucoid
n01402600 brown_algae n01403457 kelp
n01402600 brown_algae n01404365 fucoid
n01404628 rockweed n01405616 bladderwrack
n01404628 rockweed n01405007 fucus
n01404628 rockweed n01405616 bladderwrack
n01404628 rockweed n01405007 fucus
n01404628 rockweed n01405616 bladderwrack
n01404628 rockweed n01405007 fucus
n01404628 rockweed n01405616 bladderwrack
n01404628 rockweed n01405007 fucus
n01404628 rockweed n01405616 bladderwrack
n01404628 rockweed n01405007 fucus
n01340935 reovirus n01341090 rotavirus
n01340935 reovirus n01341090 rotavirus
n01340935 reovirus n01341090 rotavirus
n08659446 field n08659861 oilfield
n01387065 protoctist n01389507 protozoan
n01387065 protoctist n01397114 alga
n01387065 protoctist n01389507 protozoan
n0

n13879320 triangle n13880199 isosceles_triangle
n13879320 triangle n13879816 acute_triangle
n13879320 triangle n13880551 right_triangle
n13879320 triangle n13880704 scalene_triangle
n13879320 triangle n13919547 wedge
n13879320 triangle n13880415 obtuse_triangle
n13879320 triangle n13880199 isosceles_triangle
n13883603 spherical_polygon n13883763 spherical_triangle
n13883603 spherical_polygon n13883763 spherical_triangle
n13883603 spherical_polygon n13883763 spherical_triangle
n13883603 spherical_polygon n13883763 spherical_triangle
n13879126 quadrilateral n13881512 trapezoid
n13879126 quadrilateral n13881512 trapezoid
n13879126 quadrilateral n13881512 trapezoid
n13881175 parallelogram n13882961 rhombus
n13881175 parallelogram n13882961 rhombus
n13881175 parallelogram n13882961 rhombus
n13866827 concave_polygon n13867005 reentrant_polygon
n13866827 concave_polygon n13867005 reentrant_polygon
n13866827 concave_polygon n13867005 reentrant_polygon
n13866827 concave_polygon n13867005 reentr

n13864153 convex_shape n13902793 taper
n13864153 convex_shape n13902048 ridge
n13919685 projection n13918387 tongue
n13919685 projection n13918274 tail
n13919685 projection n13894434 bulge
n13919685 projection n13919919 keel
n13894434 bulge n05541509 frontal_eminence
n13894434 bulge n13895262 belly
n13894434 bulge n05541509 frontal_eminence
n13894434 bulge n13895262 belly
n08616050 pasture n08547468 cow_pasture
n08616050 pasture n08547468 cow_pasture
n04970059 purple n04970470 lavender
n04970059 purple n04970631 reddish_purple
n04970059 purple n04970470 lavender
n04970059 purple n04970631 reddish_purple
n04970758 violet n04970398 indigo
n04970758 violet n04970398 indigo
n04970631 reddish_purple n04970312 Tyrian_purple
n04970631 reddish_purple n04970312 Tyrian_purple
n04970631 reddish_purple n04970312 Tyrian_purple
n05467758 astrocyte n05468098 protoplasmic_astrocyte
n05467758 astrocyte n05468098 protoplasmic_astrocyte
n14974264 paper n14975598 papyrus
n03314028 face_card n04033425 quee

In [ ]:
hier_edges = []
parallel_edges = []
self_edges =[] 
for k, v in adjs.items():
    if k in [0, 9]:
        continue
    self_edges.append([k, k])
    if len(v) == 0:
        continue
    for vv in v:
        if vv in [0, 9]:
            continue
        hier_edges.append([k, vv]) 
    v = sorted(v)
    for i in range(len(v)):
        for j in range(i+1, len(v)): 
            if i!=j:
                if v[i] in [0, 9] or v[j] in [0, 9]:
                    continue
                parallel_edges.append([v[i], v[j]])


In [188]:
mat = sio.loadmat('directed-hierarchy-nell-graph.mat')
a, b = mat['edges']

In [195]:
js = json.load(open('imagenet-induced-graph.json', 'r'))

# 添加两个dummy nodes
word_vectors = js['vectors']
word_dim = len(word_vectors[0])
word_vectors.append(list(np.zeros(word_dim)))

# 将NELL图划分成多个子图 (无效）



In [86]:
import xml.etree.ElementTree as ET
import os
import pickle as pkl

srcfile = '/home/zzc/exp/zsl_code/zsl-gcn-pth/data/list/structure_released.xml'
tree = ET.parse(srcfile)
root = tree.getroot()  # root[0]:releaseData, root[1]:synset
start = root[1]

js = json.load(open('imagenet-dense-grouped-graph.json'))
wnids = js['wnids']
# ids_rev = {v:k for k,v in ids.items()}
wordnet_dict = {wnid:i for i,wnid in enumerate(wnids)}  #32324

def add_edge_dfs(node):
    edges = []
    vertice = [node.attrib["wnid"]]
    if len(node) == 0:
        return vertice, edges
    for child in node:
        if child.tag != "synset":
            print(child.tag)

        edges.append((node.attrib["wnid"], child.attrib["wnid"]))
        child_ver, child_edge = add_edge_dfs(child)
        edges.extend(child_edge)
        vertice.extend(child_ver)

    return vertice, edges

id_map = {wnid:i for i,wnid in enumerate(wnids)}  #32324
last = len(wnids)
id_map['fa11misc'] = last
id_map['fall11'] = last+1

adjs = [[] for i in range(len(id_map.keys()))]
nodes = [root[1]]
l = 0
save = None
while l < len(nodes):
    node = nodes[l]
    a = node.attrib["wnid"]
    a = id_map[a]
    adjs[a].append(a)
    for child in node:
        if child.tag != "synset":
            print(child.tag)
        b = id_map[child.attrib["wnid"]]
        adjs[a].append(b)
        if child not in nodes:
            nodes.append(child)
    l+=1


In [102]:
adjs = [[] for i in range(len(id_map.keys()))]
nodes = [root[1]]
l = 0
save = None
while l < len(nodes):
    node = nodes[l]
    a = node.attrib["wnid"]
    a = id_map[a]
    adjs[a].append(a)
    for child in node:
        if child.tag != "synset":
            print(child.tag)
        b = id_map[child.attrib["wnid"]]
        adjs[a].append(b)
        if child not in nodes:
            nodes.append(child)
    l+=1
    

In [105]:
for a, b in enumerate(adjs):
    adjs[a] = list(set(b))
edges = []
for a, b in enumerate(adjs):
    for bb in b:
        edges.append([a, bb])
print(len(edges))

67169


In [107]:
adjs_r = [[] for i in range(len(id_map.keys()))]
for a, b in edges:
    adjs_r[b].append(a)


In [108]:
cnt = [len(a) for a in adjs]
cnt_r = [len(a) for a in adjs_r]

0 29
1 1
2 29747
3 2523
4 25
5 1


In [157]:
# wordnet 增加层级

In [158]:
mat = sio.loadmat('/home/zzc/exp/zsl_code/19CVPR_GCN_imagenet_DGP/materials/imagenet-multi-weight-graph-aux-edges.mat')
adjs = [[] for i in range(len(mat['wnids']))]
adjs_r = [[] for i in range(len(mat['wnids']))]
for a, b in mat['edges']:
    adjs[a].append(b)
    adjs_r[b].append(a)
    


In [165]:
# 统计图上结点深度,添加边

from collections import Counter
depth = {i:0 for i in range(len(mat['wnids']))}
# 循环多次直至深度不再更新
for _ in range(10):
    for k,v in enumerate(adjs_r):
        for vv in v:
            if vv != k:
                depth[vv] = max(depth[k]+1, depth[vv])
    print(Counter(depth.values()))


Counter({1: 14878, 0: 6964})
Counter({2: 13531, 0: 6964, 1: 1347})
Counter({3: 11547, 0: 6964, 2: 1984, 1: 1347})
Counter({4: 10673, 0: 6964, 2: 1984, 1: 1347, 3: 874})
Counter({5: 10101, 0: 6964, 2: 1984, 1: 1347, 3: 874, 4: 572})
Counter({6: 9065, 0: 6964, 2: 1984, 1: 1347, 5: 1036, 3: 874, 4: 572})
Counter({7: 8667, 0: 6964, 2: 1984, 1: 1347, 5: 1036, 3: 874, 4: 572, 6: 398})
Counter({8: 8209, 0: 6964, 2: 1984, 1: 1347, 5: 1036, 3: 874, 4: 572, 7: 458, 6: 398})
Counter({9: 7044, 0: 6964, 2: 1984, 1: 1347, 8: 1165, 5: 1036, 3: 874, 4: 572, 7: 458, 6: 398})
Counter({0: 6964, 10: 6795, 2: 1984, 1: 1347, 8: 1165, 5: 1036, 3: 874, 4: 572, 7: 458, 6: 398, 9: 249})


In [166]:
save_mat = {}
for k, v in mat:
    save_mat[k] = v
save_mat[]

dict_keys(['__header__', '__version__', '__globals__', 'edges', 'hops', 'semantic_dis', 'visual_dis', 'wnids', 'aux_edges', 'descriptions'])